In [0]:
from pyspark.sql import functions as F
import urllib

# Define file type
file_type = "csv"
# Whether the file has a header
first_row_is_header = "True"
# Delimiter used in the file
delimiter = ","
# Read the CSV file to spark dataframe
aws_keys_df = spark.read.format(file_type)\
.option("header", first_row_is_header)\
.option("sep", delimiter)\
.load("dbfs:/FileStore/tables/PropertyFileAWS.csv")
print(aws_keys_df.columns)
# Get the AWS access key and secret key from the spark dataframe
ACCESS_KEY = aws_keys_df.where(F.col('User')=='databricks').select('Access key ID').collect()[0]['Access key ID']
# print(ACCESS_KEY)
SECRET_KEY = aws_keys_df.where(F.col('User')=='databricks').select('Secret access key').collect()[0]['Secret access key']
# Encode the secrete key
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

['User', 'Access key ID', 'Secret access key', 'Bucket Name', 'Mount Name']


In [0]:
# AWS S3 bucket name
AWS_S3_BUCKET =aws_keys_df.where(F.col('User')=='databricks').select('Bucket Name').collect()[0]['Bucket Name']

# Mount name for the bucket
MOUNT_NAME = aws_keys_df.where(F.col('User')=='databricks').select('Mount Name').collect()[0]['Mount Name']

dbutils.fs.mount(f"s3a://{ACCESS_KEY}:{ENCODED_SECRET_KEY}@{AWS_S3_BUCKET}", f"/mnt/{MOUNT_NAME}")
display(dbutils.fs.ls(f"/mnt/{MOUNT_NAME}"))

monisha-crm-bucket


path name size modificationTime dbfs:/mnt/monisha-crm-bucket/YelpDataset/ YelpDataset/ 0 0 dbfs:/mnt/monisha-crm-bucket/images/ images/ 0 0 dbfs:/mnt/monisha-crm-bucket/profile_pic_1.jpg profile_pic_1.jpg 5658 1682945696000

In [0]:
df_user= spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_user.json")
# df_user.write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/user.parquet")
df_user = spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/user.parquet")

df_business= spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_business.json")
# df_business.write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/business.parquet")
df_business = spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/business.parquet")

df_review=spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_review.json")
# df_review.write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/review.parquet")
df_review  = spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/review.parquet")

df_tip=spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_tip.json")
# df_tip.write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/tip.parquet")
df_tip = spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/tip.parquet")

df_checkin=spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_checkin.json")
# df_checkin.write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/checkin.parquet")
df_checkin = spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/checkin.parquet")




In [0]:
df_tip=spark.read.parquet("dbfs:/FileStore/tables/parquet_schema/tip.parquet")

# print ('Total number of records in TIP DATASET is: ',df_tip.count())
from pyspark.sql.functions import to_date,date_format

df_tip = df_tip.withColumn("tip_year",to_date(df_tip.date,"YYYY"))
df_tip = df_tip.withColumn("tip_month",date_format(df_tip.date,"MMMM"))
df_tip = df_tip.withColumn("tip_year",date_format(df_tip.date,"dd"))
df_tip = df_tip.withColumn("tip_Business_Date",date_format(df_tip.date,"MM/dd/yyyy"))
df_tip = df_tip.withColumn("tip_Business_time",date_format(df_tip.date,"hh:mm:ss"))

display(df_tip)
#df_tip.select('tip_year').distinct().show()

business_id compliment_count date text user_id tip_year tip_month tip_Business_Date tip_Business_time xhlzD6EnttQ9U02Y9YqQ9A 0 2019-07-19 22:16:51 Best Austrian/German Bakery in the area. CIRpuX0vB0mXDj2BlWUaCw 19 July 07/19/2019 10:16:51 hGb-yA-llJ7hnw9NyzE52A 0 2019-07-25 02:07:04 Nice nice nice apelYpgog78slqcjE7hM4Q 25 July 07/25/2019 02:07:04 8tJWgFe3ztfxYg3YWcw3rA 0 2019-08-01 03:33:57 They are super busy seems like good business, I specifically go to Andy v-zu7ziPhmML_DK1uC27VA 01 August 08/01/2019 03:33:57 2P-pvj_jo0SxNe6jih6sOA 0 2017-10-20 23:48:35 Really great food. Super fresh. JZ-N7zFC3-iNYg-Ky8KGFQ 20 October 10/20/2017 11:48:35 22uHGWZ2WkhvmZDVBGcdEQ 0 2019-08-28 15:11:49 Good food, clean environment, large portion, and great price! Kv7hxvb-7ZQeblXDpjofvQ 28 August 08/28/2019 03:11:49 CYwC5OjwCN6ib_AQDxi3Ow 0 2013-09-09 04:13:02 Always get animal fries after a long hike :) gGlACxJ06r-F2nqCU97_Uw 09 September 09/09/2013 04:13:02 G8I9weN2VpCAHs2UEmwf2g 1 2018-05-15 17:46:52 A little slice of Brooklyn in Nashville... Z5lN4IQnWW7WppuolAtdOg 15 May 05/15/2018 05:46:52 3lNXuyquPs-hhJ6Wf60woQ 0 2018-05-17 18:53:40 As the other reviewers noted, double and triple check your final bill. They just tried to sneak a $20 fuel charge even though I returned the car with a FULL tank. When I confronted the agent, he played dumb and said "oh, I wonder how that got on the bill?" 

Thieves and liars at AVIS/BUDGET!!!!!!! Z5lN4IQnWW7WppuolAtdOg 17 May 05/17/2018 06:53:40 bW3Z2Qp2rIIfZwBVP3j4Ng 0 2019-09-13 14:52:07 Great b1FHdEBl_Ci0K3nZaa4zHQ 13 September 09/13/2019 02:52:07 gbMKr0Om2E1oE5f4z0mQgg 0 2019-09-19 22:02:24 Great pizza, long delivery wait. QvYSDhsVDjqZLkqVvQTMug 19 September 09/19/2019 10:02:24 tMj79H5v1nOWmg9tsMfWiQ 0 2015-09-05 16:46:37 I don't like how the workers there scream out loud to each other in Hindi. It is offensive to me even though I am a Hindi speaker. AYgZchbVYpc1tsCJjMhnVQ 05 September 09/05/2015 04:46:37 Y_wNEd-AtDTo-jdPakoCZA 0 2019-11-03 03:46:29 Nice owners and you get to regulate the sugar and flavors. I'll be back soon. z2LP044YnB4_Uc4r0EqcsQ 03 November 11/03/2019 03:46:29 VmkntDoCpazOVmNIlXx0ug 0 2019-11-12 02:38:36 Beer, books and board games... what more can a person ask for?! Sk2Ut90jg9-nhpBM_fup3Q 12 November 11/12/2019 02:38:36 J564YQj-VdGBTmySI01UCA 0 2016-06-30 17:28:30 Nice and clean fast friendly service and great price TzSwsc7aagzre4F81D_yTw 30 June 06/30/2016 05:28:30 N1slCdDsZEN5ttS56S6Gag 0 2019-12-13 07:39:28 Owner is a real assholes that should learn some manners and respect. ikzxSyoxOoRZYiQHIlhNLw 13 December 12/13/2019 07:39:28 hYnMeAO77RGyTtIzUSKYzQ 0 2019-12-15 01:49:27 Great Cuban sandwich J0As9X7gho2hA2irITRejw 15 December 12/15/2019 01:49:27 FEXhWNCMkv22qG04E83Qjg 0 2019-03-07 19:23:06 Just the best and iconic place to see in NoLa SyC-BDtXnZBNVAWBbI1QCQ 07 March 03/07/2019 07:23:06 FEXhWNCMkv22qG04E83Qjg 0 2019-03-08 03:15:14 Nice server in a busy place. Fresh hot donuts. Yummy! 0ZSSxlUujHpr76ZrcDKE4g 08 March 03/08/2019 03:15:14 FEXhWNCMkv22qG04E83Qjg 0 2012-03-16 03:08:16 Beignets... Oh yes. own0M28i9pFq8PqEt0sR-Q 16 March 03/16/2012 03:08:16 AG8iUJbLefR48HCykQTBiA 0 2019-12-29 01:56:42 Amazing food and great atmosphere tN5ixpb5MDE1QLmOv-gU3Q 29 December 12/29/2019 01:56:42 TyBZCT3yOVfrJnMgG0tH4Q 0 2020-01-28 23:36:16 Hate this restaurant, never been a fan BuJ_aL92PuG5qSduIqAwUg 28 January 01/28/2020 11:36:16 Op8RPQBkiix8nDWsFvhnqw 0 2020-02-29 05:01:08 place is bad! all around service, food, drink 6kiYJgRqo5GYJGQDhbLZSw 29 February 02/29/2020 05:01:08 n_7EQxn0ciucIOJfpWVaTQ 0 2020-03-18 04:14:40 Love the pho here taste amazing!!! vmfoUf0eXQQ7bmoWuJF4og 18 March 03/18/2020 04:14:40 1rz9dGzG0K-omeL92KL0wA 0 2020-05-13 15:54:33 Roman Style Pizza Ls5RtHyzBjpsIdBL9kwyJQ 13 May 05/13/2020 03:54:33 dQfKzzK4wYzO6vR49YzF_A 0 2020-07-13 14:21:50 I love sushi , the best sushi in fishers town . Highly recommended A++++ PN3cWu927yJ27pVDjvZEIQ 13 July 07/13/2020 02:21:50 3YqUe2FTCQr0pP

In [0]:
print("number of partition",df_tip.rdd.getNumPartitions())

# #BYPARTITION
df= df_tip.write.partitionBy("tip_year").write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/Bypartion")

# #REPARTITION
df1 = df_tip.repartition(10).write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/repartion_10")
print("increased number of partitions after repartition: " + str(df1.rdd.getNumPartitions()))

# # COALESCE
df2= df_tip.coalesce(5).write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/coalesce_5")
print("reduced number of partitions after coalesce: " + str(df2.rdd.getNumPartitions()))

number of partition 8


---------------------------------------------------------------------------
AttributeError                            Traceback (most recent call last)
File <command-904773215135143>:4
      1 print("number of partition",df_tip.rdd.getNumPartitions())
      3 # #BYPARTITION
----> 4 df= df_tip.write.partitionBy("tip_year").write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/Bypartion")
      6 # #REPARTITION
      7 df1 = df_tip.repartition(10).write.mode("overwrite").parquet("dbfs:/FileStore/tables/parquet_schema/repartion_10")

AttributeError: 'DataFrameWriter' object has no attribute 'write'

In [0]:
#To create TEMP View
spark.read.json("dbfs:/mnt/monisha-crm-bucket/YelpDataset/yelp_academic_dataset_user.json").createOrReplaceTempView("user_json")

#Find the top 3 users based on their total number of reviews.
spark.sql("""SELECT name,review_count FROM user_json order by review_count desc limit 3""").show()

+------+------------+
|  name|review_count|
+------+------------+
|   Fox|       17473|
|Victor|       16978|
| Bruce|       16567|
+------+------------+



In [0]:
# Find the top 10 users with the most fans

spark.sql(  """SELECT name,fans FROM user_json order by fans desc limit 10""").show()

+-------+-----+
|   name| fans|
+-------+-----+
|   Mike|12497|
|  Katie| 3642|
|    Fox| 3493|
|Richard| 3243|
| Daniel| 3138|
|Jessica| 2627|
|  Ruggy| 2547|
|  Megan| 2451|
|    Emi| 2424|
|  Peter| 2388|
+-------+-----+



In [0]:
# to calculate top 10 categories based on review couunt
df_business.createOrReplaceTempView("business_table")
Business_based_on_reviews = spark.sql("""select distinct(categories),count(review_count) as numberOfReviews from business_table 
group by categories 
order by numberOfReviews desc limit 10""")
display(Business_based_on_reviews)

categories numberOfReviews Beauty & Spas, Nail Salons 1012 Restaurants, Pizza 935 Nail Salons, Beauty & Spas 934 Pizza, Restaurants 823 Restaurants, Mexican 728 Restaurants, Chinese 708 Mexican, Restaurants 672 Chinese, Restaurants 651 Food, Coffee & Tea 508 Beauty & Spas, Hair Salons 493

In [0]:
from pyspark.sql import functions as f
#Second method to calculate top 10 categories based on review couunt
df_business_reviews = df_business.groupBy("categories").agg(f.count("review_count").alias("total_review_count")).orderBy(f.desc("total_review_count"))

display(df_business_reviews)

categories total_review_count Beauty & Spas, Nail Salons 1012 Restaurants, Pizza 935 Nail Salons, Beauty & Spas 934 Pizza, Restaurants 823 Restaurants, Mexican 728 Restaurants, Chinese 708 Mexican, Restaurants 672 Chinese, Restaurants 651 Food, Coffee & Tea 508 Beauty & Spas, Hair Salons 493 Hair Salons, Beauty & Spas 480 Coffee & Tea, Food 473 Automotive, Auto Repair 361 Auto Repair, Automotive 351 Grocery, Food 329 Italian, Restaurants 328 Food, Grocery 306 Veterinarians, Pets 300 Ice Cream & Frozen Yogurt, Food 298 Restaurants, Italian 285 Pets, Veterinarians 285 Barbers, Beauty & Spas 281 Beauty & Spas, Barbers 280 Hotels, Hotels & Travel, Event Planning & Services 280 Hotels, Event Planning & Services, Hotels & Travel 278 Hotels & Travel, Event Planning & Services, Hotels 278 Food, Ice Cream & Frozen Yogurt 277 Event Planning & Services, Hotels, Hotels & Travel 271 Event Planning & Services, Hotels & Travel, Hotels 268 Hotels & Travel, Hotels, Event Planning & Services 256 Food, Beer, Wine & Spirits 248 Restaurants, American (New) 247 Car Rental, Hotels & Travel 240 Real Estate, Apartments, Home Services 238 American (New), Restaurants 235 Beer, Wine & Spirits, Food 231 Apartments, Real Estate, Home Services 230 Hotels & Travel, Car Rental 227 Real Estate, Home Services, Apartments 226 Home Services, Real Estate, Apartments 223 Banks & Credit Unions, Financial Services 221 Home Services, Apartments, Real Estate 220 Financial Services, Banks & Credit Unions 220 Apartments, Home Services, Real Estate 218 Automotive, Car Wash 205 American (Traditional), Restaurants 203 Restaurants, American (Traditional) 188 Car Wash, Automotive 187 Restaurants, Fast Food, Burgers 177 Bars, Nightlife 162 Nightlife, Bars 160 Restaurants, Burgers, Fast Food 154 Heating & Air Conditioning/HVAC, Home Services 154 Thai, Restaurants 152 Car Dealers, Automotive 150 Active Life, Parks 150 Local Services, Self Storage 148 Restaurants, Vietnamese 146 Barbeque, Restaurants 143 Fast Food, Restaurants, Burgers 143 Restaurants, Thai 140 Restaurants, Barbeque 140 Self Storage, Local Services 137 Seafood, Restaurants 136 Food, Bakeries 135 Automotive, Auto Parts & Supplies 135 Italian, Restaurants, Pizza 135 Parks, Active Life 134 Restaurants, Sandwiches 133 Bakeries, Food 129 Restaurants, Sandwiches, Fast Food 129 Burgers, Restaurants, Fast Food 128 Restaurants, Seafood 127 Automotive, Car Dealers 127 Movers, Home Services 127 Vietnamese, Restaurants 126 Home Services, Heating & Air Conditioning/HVAC 126 Sandwiches, Restaurants, Fast Food 123 Sandwiches, Restaurants 123 Jewelry, Shopping 122 Shopping, Jewelry 122 Sewing & Alterations, Local Services 122 Chiropractors, Health & Medical 121 Pizza, Restaurants, Italian 119 Burgers, Fast Food, Restaurants 119 Health & Medical, Chiropractors 117 Restaurants, Italian, Pizza 117 Restaurants, Indian 115 Indian, Restaurants 115 Restaurants 114 Automotive, Gas Stations 108 Auto Parts & Supplies, Automotive 106 Local Services, Pest Control 106 Gas Stations, Automotive 106 Pest Control, Local Services 106 Restaurants, Breakfast & Brunch 104 Local Services, Sewing & Alterations 103 null 103 Italian, Pizza, Restaurants 103 Home Services, Movers 103 Home Services, Plumbing 102 Restaurants, Diners 101 Arts & Entertainment, Cinema 100 Pets, Pet Stores 100 Restaurants, Pizza, Italian 100 Cinema, Arts & Entertainment 99 Diners, Restaurants 99 Breakfast & Brunch, Restaurants 98 Discount Store, Shopping 95 Pizza, Italian, Restaurants 94 Fast Food, Burgers, Restaurants 94 Pet Stores, Pets 92 Restaurants, Burgers 91 Automotive, Body Shops 89 Dry Cleaning & Laundry, Local Services, Laundry Services 88 Local Services, Appliances & Repair 88 Japanese, Restaurants 88 Body Shops, Automotive 87 Public Services & Government, Libraries 85 Burgers, Restaurants 83 Restaurants, Japanese 83 Sandwiches, Fast Food, Restaurants 83 Tree Services, Home Services 82 Appliances & Repair, Local Services 81 Libraries, Public Services & Government 81 

In [0]:
#Analyse top businesses which have over 1000 reviews
Business_based_on_reviews.createOrReplaceTempView("Business_based_on_review")
Business_moreThan_1000Reviews = spark.sql("""select categories,numberOfReviews
from Business_based_on_review where numberOfReviews >=1000""")
display(Business_moreThan_1000Reviews)

categories numberOfReviews Beauty & Spas, Nail Salons 1012

In [0]:
#Using it on SQL to filter number of restaurants by state
df_business.createOrReplaceTempView("business")
r=spark.sql("""select distinct(state),count(categories) as numberOfRestaurant 
            from business 
            where categories like '%Res%' group by state""")
display(r)


state numberOfRestaurant AZ 2722 LA 3669 NJ 3371 NV 1723 ID 1324 CA 1181 MT 1 DE 966 MO 4278 IL 990 IN 4180 TN 4385 PA 12734 AB 2413 FL 8869 XMS 1 NC 1 CO 1 HI 1

In [0]:
#Analyze the top 3 restaurants in each state.

top_3_restaurantsInEachState=spark.sql("""select * from (select categories,state,name,review_count,
ROW_NUMBER() OVER(partition by state order by review_count desc) as rank
from business_table where categories like '%Rest%')
where rank <=3""")
display(top_3_restaurantsInEachState)

categories state name review_count rank Restaurants, Cocktail Bars, Bars, Comfort Food, American (New), Sandwiches, Nightlife, Breakfast & Brunch AZ Prep & Pastry 2126 1 Tapas/Small Plates, Desserts, Cocktail Bars, Nightlife, Bars, Tacos, Mexican, Food, Restaurants, Salad AZ El Charro Cafe 1583 2 American (Traditional), Restaurants, Mexican, Latin American AZ Cafe Poca Cosa 1306 3 Mexican, Restaurants CA Los Agaves 3834 1 Cocktail Bars, Fish & Chips, Nightlife, Seafood, Restaurants, Bars CA Brophy Bros - Santa Barbara 2940 2 Seafood, Restaurants, Hawaiian, American (New), Breakfast & Brunch CA Boathouse at Hendry's Beach 2536 3 Cajun/Creole, Vegetarian, Restaurants, Tex-Mex, Cocktail Bars, Bars, Nightlife DE Border Cafe 742 1 Restaurants, Food, Breweries, American (New), Local Flavor DE Iron Hill Brewery & Restaurant 512 2 Bars, Nightlife, American (Traditional), Restaurants, Seafood DE Big Fish Grill - Riverfront 456 3 American (New), Burgers, Restaurants, Breakfast & Brunch ID Fork 1810 1 Nightlife, Latin American, Steakhouses, Seafood, Restaurants, Brazilian, Cocktail Bars, Bars ID Barbacoa Grill 1099 2 Bars, Gastropubs, Sandwiches, Nightlife, Restaurants ID Bittercreek Alehouse 998 3 Live/Raw Food, Seafood, Restaurants, Cajun/Creole LA Acme Oyster House 7568 1 Restaurants, Seafood, Cajun/Creole, Breakfast & Brunch LA Oceana Grill 7400 2 Restaurants, American (Traditional), American (New), Cafes, Breakfast & Brunch LA Ruby Slipper - New Orleans 5193 3 Food, Restaurants, Caterers, Smokehouse, Barbeque, Food Trucks, Event Planning & Services MO Pappy's Smokehouse 3999 1 Seafood, Cajun/Creole, Arts & Entertainment, Jazz & Blues, Restaurants, Nightlife, Music Venues MO Broadway Oyster Bar 2076 2 Creperies, Cafes, Restaurants, Sandwiches, Breakfast & Brunch, Gluten-Free MO Rooster - Downtown 1984 3 Restaurants, American (Traditional), Food Trucks, Burgers, Food MT MudMan Food Truck 6 1 Breakfast & Brunch, Coffee & Tea, Food, American (New), Diners, Restaurants, American (Traditional), Burgers NC IHOP 29 1 Restaurants, American (New) NJ The Farm and Fisherman Tavern 709 1 Tea Rooms, Korean, Asian Fusion, Chicken Wings, Food, Restaurants, Specialty Food NJ Dolsot House 665 2 Chicken Wings, American (Traditional), Restaurants, Nightlife, Bars, American (New) NJ The Jug Handle Inn 604 3 Restaurants, Breakfast & Brunch, Diners, Hawaiian, American (Traditional) NV Peg's Glorified Ham N Eggs 2506 1 Resorts, Event Planning & Services, Restaurants, Casinos, Arts & Entertainment, Party & Event Planning, Hotels, Venues & Event Spaces, Hotels & Travel NV Nugget Casino Resort 1576 2 Arts & Entertainment, Hotels, Party & Event Planning, Casinos, Event Planning & Services, Restaurants, Hotels & Travel NV Silver Legacy Resort Casino 1534 3 Patisserie/Cake Shop, Food, Restaurants, Bakeries, Cafes, French AB Duchess Bake Shop 486 1 Juice Bars & Smoothies, American (New), Cafes, Food, Comfort Food, Desserts, Restaurants, Canadian (New), Coffee & Tea, Breakfast & Brunch AB SugarBowl 435 2 Restaurants, Mexican AB Tres Carnales Taqueria 429 3 Buffets, Restaurants CO Two Elk Restaurant 12 1 Burgers, Bars, Restaurants, American (Traditional), Vegan, Asian Fusion, Cocktail Bars, Breakfast & Brunch, Soul Food, Sandwiches, American (New), Gastropubs, Comfort Food, Nightlife, Wine Bars, Delis FL Datz 3260 1 Breweries, Food, American (New), Beer, Wine & Spirits, Restaurants, Seafood FL Ulele 3064 2 Arts & Entertainment, Steakhouses, Restaurants FL Bern's Steak House 2924 3 Cosmetic Surgeons, Pizza, Doctors, Beauty & Spas, Nail Salons, Cosmetics & Beauty Supply, Chiropractors, Shopping, Restaurants, Health & Medical HI Cosmetic Solutions 17 1 Restaurants, Barbeque IL BEAST Craft BBQ 583 1 Restaurants, Southern, American (Traditional) IL Lotawata Creek Southern Grill 550 2 American (New), Restaurants, American (Traditional) IL Cleveland-Heath 455 3 Nightlife, Comfort Food, Restaurants, American (New), American (Traditional), Soul Food, Southern, Bars, Beer Ba

In [0]:
#list the top restaurants in a state by the number of reviews using python

list_state=r.select('state').rdd.flatMap(lambda x: x).collect()
print(list_state)

def findTop3RestaurantsInEachState(list_state):
    df_business.createOrReplaceTempView("business_table")
    for i in list_state:
        query=spark.sql('''select categories,state,name,review_count from business_table 
        where state='{}' and  categories like '%Rest%'     
        order by review_count desc limit 3'''.format(i))
        display(query)

findTop3RestaurantsInEachState(list_state)


['AZ', 'LA', 'NJ', 'NV', 'ID', 'CA', 'MT', 'DE', 'MO', 'IL', 'IN', 'TN', 'PA', 'AB', 'FL', 'XMS', 'NC', 'CO', 'HI']


categories state name review_count Restaurants, Cocktail Bars, Bars, Comfort Food, American (New), Sandwiches, Nightlife, Breakfast & Brunch AZ Prep & Pastry 2126 Tapas/Small Plates, Desserts, Cocktail Bars, Nightlife, Bars, Tacos, Mexican, Food, Restaurants, Salad AZ El Charro Cafe 1583 American (Traditional), Restaurants, Mexican, Latin American AZ Cafe Poca Cosa 1306

categories state name review_count Live/Raw Food, Seafood, Restaurants, Cajun/Creole LA Acme Oyster House 7568 Restaurants, Seafood, Cajun/Creole, Breakfast & Brunch LA Oceana Grill 7400 Restaurants, American (Traditional), American (New), Cafes, Breakfast & Brunch LA Ruby Slipper - New Orleans 5193

categories state name review_count Restaurants, American (New) NJ The Farm and Fisherman Tavern 709 Tea Rooms, Korean, Asian Fusion, Chicken Wings, Food, Restaurants, Specialty Food NJ Dolsot House 665 Chicken Wings, American (Traditional), Restaurants, Nightlife, Bars, American (New) NJ The Jug Handle Inn 604

categories state name review_count Restaurants, Breakfast & Brunch, Diners, Hawaiian, American (Traditional) NV Peg's Glorified Ham N Eggs 2506 Resorts, Event Planning & Services, Restaurants, Casinos, Arts & Entertainment, Party & Event Planning, Hotels, Venues & Event Spaces, Hotels & Travel NV Nugget Casino Resort 1576 Arts & Entertainment, Hotels, Party & Event Planning, Casinos, Event Planning & Services, Restaurants, Hotels & Travel NV Silver Legacy Resort Casino 1534

...

categories state name review_count Burgers, Bars, Restaurants, American (Traditional), Vegan, Asian Fusion, Cocktail Bars, Breakfast & Brunch, Soul Food, Sandwiches, American (New), Gastropubs, Comfort Food, Nightlife, Wine Bars, Delis FL Datz 3260 Breweries, Food, American (New), Beer, Wine & Spirits, Restaurants, Seafood FL Ulele 3064 Arts & Entertainment, Steakhouses, Restaurants FL Bern's Steak House 2924

categories state name review_count Caterers, Breakfast & Brunch, Convenience Stores, Food, Restaurants, Event Planning & Services XMS Pumpernickles Catering 5

categories state name review_count Breakfast & Brunch, Coffee & Tea, Food, American (New), Diners, Restaurants, American (Traditional), Burgers NC IHOP 29

categories state name review_count Buffets, Restaurants CO Two Elk Restaurant 12

categories state name review_count Cosmetic Surgeons, Pizza, Doctors, Beauty & Spas, Nail Salons, Cosmetics & Beauty Supply, Chiropractors, Shopping, Restaurants, Health & Medical HI Cosmetic Solutions 17

In [0]:
#Numbers of restaurants in Arizona state per city.
df_business.createOrReplaceTempView("business_table")
AZ_city_df= spark.sql('''select  distinct(city), count(categories) as numberOfRestaurants from business_table
                        where state='AZ' and categories like '%Res%'
                        group by city 
                        order by numberOfRestaurants desc''')
display(AZ_city_df)

city numberOfRestaurants Tucson 2514 Oro Valley 81 Marana 40 Green Valley 26 Vail 17 Sahuarita 17 Catalina 7 Tuscon 5 Mount Lemmon 4 South Tucson 2 TUCSON 2 tucson 1 Picture Rocks 1 Drexel Heights 1 Corona De Tucson 1 Casas Adobes 1 Corona de Tucson 1 Valencia West 1

In [0]:
#Most rated Italian restaurant in Philadelphia.
df_business.createOrReplaceTempView("business_table")
Italian_rest_4Ratings= spark.sql('''select  city,state,categories,review_count,stars  from business_table
                      where categories like '%Ital%'  and city='Philadelphia'
                      and stars >= 4 and review_count >=100
                      order by stars desc''')
display(Italian_rest_4Ratingscities)


city state categories review_count stars Philadelphia PA Convenience Stores, Italian, Specialty Food, Mexican, Restaurants, Food 219 5.0 Philadelphia PA Restaurants, Italian 578 4.5 Philadelphia PA Restaurants, Bars, Performing Arts, Gluten-Free, Wine Bars, Nightlife, Italian, Arts & Entertainment 437 4.5 Philadelphia PA Bars, Gelato, Breakfast & Brunch, Italian, Food, Nightlife, Restaurants, Pizza 205 4.5 Philadelphia PA Italian, Pizza, Restaurants 145 4.5 Philadelphia PA Food, Salad, Nightlife, Comfort Food, Pasta Shops, Italian, Bars, Restaurants, Specialty Food 160 4.5 Philadelphia PA Mediterranean, Restaurants, Pizza, Italian 2893 4.5 Philadelphia PA Restaurants, American (Traditional), Italian 213 4.5 Philadelphia PA Restaurants, Italian 155 4.5 Philadelphia PA Restaurants, Italian 136 4.5 Philadelphia PA Italian, Sandwiches, Pizza, Restaurants 107 4.5 Philadelphia PA Italian, Cuban, Restaurants 489 4.5 Philadelphia PA Food, Coffee & Tea, Pizza, Restaurants, Italian 208 4.5 Philadelphia PA Pizza, Restaurants, Nightlife, Italian, Bars, Gelato, Food, Wine Bars 243 4.5 Philadelphia PA Restaurants, Italian 141 4.5 Philadelphia PA Gluten-Free, Pizza, Venues & Event Spaces, Italian, Restaurants, Event Planning & Services 163 4.5 Philadelphia PA Cafes, Cafeteria, Restaurants, Italian, Gelato, Food 111 4.5 Philadelphia PA Sandwiches, Cheese Shops, Meat Shops, Italian, Specialty Food, Restaurants, Food 250 4.5 Philadelphia PA Restaurants, Gelato, Coffee & Tea, Food, Italian, Bakeries 1138 4.5 Philadelphia PA Mediterranean, Restaurants, Wine Bars, Bars, Nightlife, Italian 352 4.5 Philadelphia PA Wine Bars, Nightlife, Bars, American (New), Restaurants, Italian, Spanish 160 4.5 Philadelphia PA American (New), Bars, Wine Bars, Italian, Restaurants, Comfort Food, Seafood, Nightlife 408 4.5 Philadelphia PA Street Vendors, Food, Restaurants, Pizza, Food Trucks, Italian 142 4.5 Philadelphia PA Italian, Pasta Shops, Restaurants, Food, Specialty Food 177 4.5 Philadelphia PA Italian, Restaurants 137 4.5 Philadelphia PA Restaurants, Italian 386 4.5 Philadelphia PA Bars, Tapas/Small Plates, Cocktail Bars, Nightlife, Italian, Restaurants 144 4.5 Philadelphia PA Food, Food Trucks, Caterers, Chinese, Asian Fusion, Restaurants, Japanese, Event Planning & Services, Italian, Steakhouses, Dim Sum, Street Vendors 173 4.5 Philadelphia PA Pizza, Pasta Shops, Food, Specialty Food, Restaurants, Italian 103 4.5 Philadelphia PA Event Planning & Services, Food, Italian, Coffee & Tea, Sandwiches, Restaurants, Caterers, Delis 101 4.5 Philadelphia PA Italian, Restaurants 148 4.5 Philadelphia PA French, Spanish, Tapas Bars, Cafes, Restaurants, Wine Bars, Modern European, Bars, Nightlife, Italian, Comedy Clubs, Greek, American (New) 880 4.5 Philadelphia PA Pasta Shops, Specialty Food, Food, Italian, Restaurants 120 4.5 Philadelphia PA Restaurants, Chinese, Italian 190 4.5 Philadelphia PA Event Planning & Services, Venues & Event Spaces, Cupcakes, Coffee Roasteries, Italian, Food, Bakeries, Coffee & Tea, Restaurants 304 4.5 Philadelphia PA Restaurants, Sandwiches, Italian 387 4.5 Philadelphia PA Restaurants, Italian 217 4.5 Philadelphia PA Restaurants, Tapas/Small Plates, Italian, Szechuan, Cocktail Bars, Pizza, Chinese, Bars, Nightlife 610 4.5 Philadelphia PA Pizza, Italian, Salad, Restaurants 566 4.5 Philadelphia PA Italian, Restaurants, Sandwiches, Food Delivery Services, Salad, Food, Pizza, Gluten-Free 604 4.0 Philadelphia PA Pizza, American (Traditional), Restaurants, Italian 176 4.0 Philadelphia PA Restaurants, Italian, Sandwiches, Pizza 312 4.0 Philadelphia PA Desserts, Event Planning & Services, Caterers, Vegetarian, Pizza, Restaurants, Food, Italian, Venues & Event Spaces 266 4.0 Philadelphia PA Breakfast & Brunch, American (New), Mexican, French, Restaurants, Italian 1094 4.0 Philadelphia PA Italian, Food, Nightlife, Pizza, Bars, Cocktail Bars, Beer, Wine & Spirits, Restaurants 729 4.0 Philadelphia PA Pizza, Italian, Restaurants, Gluten-Free 954 4.0 Phi